In [2]:
import pandas as pd
pd.options.mode.chained_assignment = None  # default='warn'
import numpy as np
import seaborn as sns

import matplotlib
import matplotlib.pyplot as plt
plt.style.use('ggplot')
from matplotlib.pyplot import figure

%matplotlib inline
matplotlib.rcParams['figure.figsize'] = (12,8) # Adjusts the configuration of the plots we create

#To look at all your data
pd.set_option('display.max_rows', None)


fifa_data_raw = pd.read_csv('fifa21.csv',low_memory=False)

fifa_data_raw.info() #17,125 rows and 107 columns

#list(fifa_data_raw.columns)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17125 entries, 0 to 17124
Columns: 107 entries, ID to Gender
dtypes: float64(10), int64(45), object(52)
memory usage: 14.0+ MB


In [3]:
#The data is too large and for convenience a new dataframe with a 13 columns is created.

fifa = fifa_data_raw[['ID','Name','Age','Gender','Club','Height','Weight','Joined','Value','Wage','Release Clause','Hits','Team & Contract']]
#fifa[['Club','Team & Contract','Joined']]#

# Lets clean the data by answering some questions.

# Check for null values
fifa.isnull().sum()

# There are 23 missing values in the column Club and 58 missing values in the column Joined. 
# Explore the raw data to see if these missing values can be taken from any other columns in the table.
# The column Team and Contract can be used to get missing values in Club and Joined column.



ID                  0
Name                0
Age                 0
Gender              0
Club               23
Height              0
Weight              0
Joined             58
Value               0
Wage                0
Release Clause      0
Hits                0
Team & Contract     0
dtype: int64

In [4]:
# Lets fetch the year from the Team & Contract column using a regular expression and then populate only the cells with Null values.

fifa['temp'] = fifa['Team & Contract'].str.findall(r'\b(\d{4})\b').str[0]
fifa['Joined'] = fifa['Joined'].fillna(fifa['temp'])


# Still 10 entries are NULL. These players are not under any contract and they are FREE (as indicated in Teams & Contract column).
# Thus null value is assigned. Lets drop these entries.

# Drop rows which players are labelled as free players
fifa.dropna(subset=['Joined'], inplace=True)


# Drop rows which players are labelled as free players
fifa = fifa[~fifa['Team & Contract'].str.contains('Free', na=False)]

# Check for null values
fifa.isnull().sum()




ID                 0
Name               0
Age                0
Gender             0
Club               0
Height             0
Weight             0
Joined             0
Value              0
Wage               0
Release Clause     0
Hits               0
Team & Contract    0
temp               0
dtype: int64

In [5]:
# Question 1: Do the height and weight columns have the appropriate data types?

#Check the data types of the variable Height and Weight
# Data types of variables
fifa[['Height','Weight']].dtypes #Data type is object which refers to string, this has to be changed to integer


# Top 5 rows of Height and Weight
fifa[['Height','Weight',]].head()


#Convert Height from 6'7" string to 6.7 float
def height_numeric (height_str):
    feet, inches = height_str.split("'")
    feet = int(feet)
    inches = float(inches.strip('\"'))
    height = feet + inches/12
    return height

# Transform
fifa['Height'] = fifa['Height'].apply(height_numeric)

#Change the Weight column to int data type and omit the string 'lbs'
x = fifa['Weight'].str.findall('^(.*)(?=lbs)').str[0].astype(int)

fifa['Weight'] = x

fifa[['Weight','Height']].dtypes



Weight      int64
Height    float64
dtype: object

In [6]:
# Question 2: Can you clean and transform the value, wage and release clause columns into columns of integers?

fifa[['Wage','Release Clause','Value']].head()
    
# Function to convert string value to integer
def convert_money(money_str):
    multiplier = 1  # Default multiplier for values without 'K' or 'M' suffix

    if money_str.endswith('K'):
        multiplier = 1000
        money_str = money_str[:-1]  # Remove the 'K' suffix
    elif money_str.endswith('M'):
        multiplier = 1000000
        money_str = money_str[:-1]  # Remove the 'M' suffix

    money_str = money_str[1:]  # Remove the euro symbol

    return int(float(money_str) * multiplier) # Return integer value


# Apply the conversion function to the 'Value' column
fifa['Value'] = fifa['Value'].apply(convert_money)
fifa['Wage'] = fifa['Wage'].apply(convert_money)
fifa['Release Clause'] = fifa['Release Clause'].apply(convert_money)

# Show the data types
fifa[['Value','Wage','Release Clause']].dtypes


fifa[['Wage','Release Clause','Value']].head()

Wage  Release Clause    Value
0   7000               0   625000
1   7000         1100000   600000
2  15000               0  1100000
3      0               0        0
4  12000         7200000  5500000

In [7]:
# Question 3: Can you separate the joined column into year, month and day column?

# Convert the 'Joined' column to datetime type
fifa['Joined'] = pd.to_datetime(fifa['Joined'],format='mixed')

# Extract year, month, and day components into separate columns
fifa['Year'] = fifa['Joined'].dt.year
fifa['Month'] = fifa['Joined'].dt.month
fifa['Day'] = fifa['Joined'].dt.day

# Top 5 rows of 'Joined', 'Year', 'Month' and 'Day' columns
fifa[['Joined','Year','Month','Day']].head()



Joined  Year  Month  Day
0 2008-07-01  2008      7    1
1 2014-07-19  2014      7   19
2 2016-01-07  2016      1    7
3 2009-01-01  2009      1    1
4 2018-07-16  2018      7   16

In [8]:
# Question 4: How can you remove the newline characters from the Hits column?

# Remove newline characters from the 'Hits' column
fifa['Hits'] = fifa['Hits'].str.replace('\n', '')



In [8]:
# Question 5: Can you separate the Team & Contract column into separate Team and Contract columns?

#r'(.+?)(?:\s+(\d{4}(?:\s*~\s*\d{4})?))?(\s*$)'
x = fifa['Team & Contract'].str.split(r'(.+?)(?:\s+(\d{4}(?:\s*~\s*\d{4})?))?(\s*$)')#[1:]

fifa['Team'] = x.str[1]
fifa['Contract'] = x.str[2]

fifa[['Team & Contract','Team','Contract']]



Team & Contract  \
0                                    Udinese 2008 ~ 2016   
1                                  KAS Eupen 2014 ~ 2019   
2                              Coventry City 2016 ~ 2020   
3                                        Sunderland 2009   
4                                Vissel Kobe 2018 ~ 2021   
5                           Alemannia Aachen 2011 ~ 2012   
6                              Fenerbahçe SK 2019 ~ 2020   
7                          Manchester United 1990 ~ 2014   
8                          Manchester United 1991 ~ 2011   
9                          Manchester United 1993 ~ 2013   
10                                   Everton 2005 ~ 2013   
12                                 LA Galaxy 2011 ~ 2022   
13                          Newcastle United 2010 ~ 2011   
14                                FC Bayern München 2008   
15                        Milton Keynes Dons 2010 ~ 2011   
16                                        Hull City 2009   
17                           Pohang Steelers 2005 ~ 2013   
18                            Leicester City 2015 ~ 2016   
19                                    VfB Stuttgart 2010   
21                      FC Anzhi Makhachkala 2011 ~ 2013   
22                                     Inter 1995 ~ 2014   
23                                 Sydney FC 2012 ~ 2014   
24                           Montreal Impact 2012 ~ 2013   
25                                            Milan 2009   
26                                  Juventus 2019 ~ 2021   
27                                         Juventus 2010   
28                                            Parma 2007   
29                                     Milan 2001 ~ 2012   
30                                     Milan 2016 ~ 2020   
31                            CF Estrela da Amadora 2008   
32                                      Roma 1993 ~ 2017   
33                                  Botafogo 2012 ~ 2014   
34                           Manchester City 2010 ~ 2011   
35                                     FC Barcelona 2008   
37                       Paris Saint-Germain 2008 ~ 2011   
38                       Paris Saint-Germain 2009 ~ 2011   
39                                Manchester United 2008   
40                              Ipswich Town 2011 ~ 2012   
41                                      Ajax 2020 ~ 2021   
42                                  Manchester City 2009   
43                         Borussia Dortmund 2002 ~ 2018   
44                          Bolton Wanderers 2014 ~ 2016   
45                                SL Benfica 2014 ~ 2018   
46                                Stoke City 2015 ~ 2017   
47                            Newport County 2020 ~ 2021   
48                             Burton Albion 2013 ~ 2014   
49                               Aston Villa 2006 ~ 2013   
50                                Rio Ave FC 2008 ~ 2021   
51                        New York Red Bulls 2016 ~ 2023   
52                           SD Ponferradina 2017 ~ 2021   
53                                   Reading 2018 ~ 2019   
55                       Bayer 04 Leverkusen 2010 ~ 2012   
56                             Internacional 2013 ~ 2015   
57                              Bayer 04 Leverkusen 2010   
58                              RCD Espanyol 2012 ~ 2014   
59                                  Cracovia 2010 ~ 2012   
60                                   FC Sion 2012 ~ 2014   
61                               New York Red Bulls 2009   
62                                            Milan 2007   
63                                     Lecce 2009 ~ 2012   
64                         Stade Brestois 29 2012 ~ 2014   
65                                Stoke City 2012 ~ 2013   
66                          Doncaster Rovers 2006 ~ 2017   
67                                 Liverpool 1996 ~ 2013   
68                          New York City FC 2015 ~ 2023   
69                                  FC Porto 2015 ~ 2020   
70                   